<a href="https://colab.research.google.com/github/vinayprabhu/Fun_random/blob/master/Video_with_SynsinNMuseNet.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# First, clone the repo to your work folder. All my side projects reside in GDrive and I use Colab to run these notebooks


In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import pandas as pd
%matplotlib inline
from google.colab import drive
drive.mount('/gdrive')
import os
os.chdir('/gdrive/My Drive/Synsin/synsin/demos')

Drive already mounted at /gdrive; to attempt to forcibly remount, call drive.mount("/gdrive", force_remount=True).


In [0]:
%matplotlib inline
import matplotlib.pyplot as plt

# import quaternion # This is a tricky one!
import numpy as np

import os
os.chdir("..")
os.environ['DEBUG'] = '0'

import torch
import torch.nn as nn
import torchvision.transforms as transforms
from models.networks.sync_batchnorm import convert_model
from models.base_model import BaseModel
from options.options import get_model

In [3]:
!pip install numpy numpy-quaternion # If you don't have this pre-installed
import quaternion

<h2>Set up the models</h2>

In [0]:
# Download the model
# !wget https://dl.fbaipublicfiles.com/synsin/checkpoints/realestate/zbufferpts.pth


In [6]:
torch.backends.cudnn.enabled = True
# REALESTATE
MODEL_PATH = 'zbufferpts.pth'


BATCH_SIZE = 1

opts = torch.load(MODEL_PATH)['opts']
opts.render_ids = [1]

model = get_model(opts)

torch_devices = [int(gpu_id.strip()) for gpu_id in opts.gpu_ids.split(",")]
device = 'cuda:' + str(torch_devices[0])

if 'sync' in opts.norm_G:
    model = convert_model(model)
    model = nn.DataParallel(model, torch_devices[0:1]).cuda()
else:
    model = nn.DataParallel(model, torch_devices[0:1]).cuda()


#  Load the original model to be tested
model_to_test = BaseModel(model, opts)
model_to_test.load_state_dict(torch.load(MODEL_PATH)['state_dict'])
model_to_test.eval()

print("Loaded model")

Loading model %s ... 
RESNET encoder
RESNET decoder
['1.0_l1', '10.0_content']
Loaded model


# Idea: Use [Quaternion slerp](https://en.wikipedia.org/wiki/Slerp#Quaternion_Slerp) to generate the panning camera effect!

In [111]:
from PIL import Image
from scipy.spatial.transform import Rotation as R
from scipy.spatial.transform import Slerp
# Setup the fixed keyframe rotations and times:
# N_random_rotations=3
Ratio_oversample=100
key_rots = R.random(N_random_rotations, random_state=2342345)
key_rots=R.from_rotvec(np.concatenate([np.pi/5 *np.eye(3),np.fliplr(I)]))
key_times = list(np.arange(6))
# Create the interpolator object:
slerp = Slerp(key_times, key_rots)
# Interpolate the rotations at the given times:

times = list(np.arange(0,max(key_times)+1/Ratio_oversample,1/Ratio_oversample))
interp_rots = slerp(times)
# The keyframe rotations expressed as Euler angles:
key_rots.as_euler('xyz', degrees=True)

# The interpolated rotations expressed as Euler angles. 
# These agree with the keyframe rotations at both 
# endpoints of the range of keyframe times.
interp_rots.as_euler('xyz', degrees=True)

array([[3.60000000e+01, 0.00000000e+00, 0.00000000e+00],
       [3.56524163e+01, 3.48263727e-01, 1.11991309e-01],
       [3.53054948e+01, 6.97199794e-01, 2.21873911e-01],
       ...,
       [2.20561613e+01, 4.44510287e-01, 8.66305722e-02],
       [2.22779983e+01, 2.22171259e-01, 4.37453865e-02],
       [2.25000000e+01, 1.27222187e-14, 1.40035574e-15]])

# Main loop to generate the trippy images using the Synsin models

In [0]:
%%capture
import imageio
import matplotlib.animation as animation

fig = plt.figure(figsize=(10,10))
transform = transforms.Compose([
    transforms.Resize((256,256)),
    transforms.ToTensor(),
    transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))])

im = Image.open('gf.jpg')
im = transform(im)
rotation_matrix_degrees=interp_rots.as_euler('xyz', degrees=True)
rotation_matrix=interp_rots.as_euler('xyz', degrees=False)
ims = []
for rot_ind in range(rotation_matrix.shape[0]):

  # Parameters for the transformation
  phi=rotation_matrix[rot_ind,0]
  theta=rotation_matrix[rot_ind,1]
  psi=rotation_matrix[rot_ind,2]

  tx = 0.1
  ty = 0.1
  tz = 0.1

  RT = torch.eye(4).unsqueeze(0)
  # Set up rotation
  RT[0,0:3,0:3] = torch.Tensor(quaternion.as_rotation_matrix(quaternion.from_rotation_vector([phi, theta, psi])))
  # Set up translation
  RT[0,0:3,3] = torch.Tensor([tx, ty, tz])

  batch = {
      'images' : [im.unsqueeze(0)],
      'cameras' : [{
          'K' : torch.eye(4).unsqueeze(0),
          'Kinv' : torch.eye(4).unsqueeze(0)
      }]
  }

  # Generate a new view at the new transformation
  with torch.no_grad():
      pred_imgs = model_to_test.model.module.forward_angle(batch, [RT])
      depth = nn.Sigmoid()(model_to_test.model.module.pts_regressor(batch['images'][0].cuda()))
  plt.axis('off')
  im_out =plt.imshow(pred_imgs[0].squeeze().cpu().permute(1,2,0).numpy() * 0.5 + 0.5, animated=True)
  # plt.title(str(rotation_matrix_degrees[rot_ind,:]))
  ims.append([im_out])


# Stitch up the images as an mp4 and view it!

In [117]:
ani = animation.ArtistAnimation(fig, ims, interval=50, blit=True,
                                repeat_delay=1000)
ani.save('GF.mp4')
from IPython.display import HTML
from base64 import b64encode
mp4 = open('GF.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

Icing on the cake. Generate an mp3 from musenet


Link: https://openai.com/blog/musenet/#fn2

In [119]:
import moviepy.editor as mp
video.write_videofile("GF_with_music.mp4",audio="MuseNet_Mozart_Godfather.mp3")	

[MoviePy] >>>> Building video GF_with_music.mp4
[MoviePy] Writing video GF_with_music.mp4


100%|█████████▉| 501/502 [00:12<00:00, 39.36it/s]


[MoviePy] Done.
[MoviePy] >>>> Video ready: GF_with_music.mp4 



In [120]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('GF.mp4','rb').read()
data_url = "data:GF_with_music.mp4/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)